In [ ]:
# !pip install kaggle --quiet
# %env KAGGLE_USERNAME=aryagoyal
# %env KAGGLE_KEY=912b4f37f24f352ad1e0667b90d8ed7d
# !kaggle datasets download -d reubensuju/celeb-df-v2
# !unzip /content/celeb-df-v2.zip
#base_directory = "/content"

In [1]:
!pip install kaggle

Defaulting to user installation because normal site-packages is not writeable


In [5]:
!which kaggle

which: no kaggle in (/share/apps/pyenv/py3.9/bin:/share/apps/pyenv/py3.9/condabin:/opt/go/1.20.3/bin:/opt/go/1.20.3/bin:/usr/local/bin:/usr/bin:/usr/local/sbin:/usr/sbin:/opt/slurm/bin)


In [6]:
!~/.local/bin/kaggle datasets download -d reubensuju/celeb-df-v2 -p /scratch/ag9961


Dataset URL: https://www.kaggle.com/datasets/reubensuju/celeb-df-v2
License(s): unknown
100%|█████████████████████████████████████▉| 9.28G/9.29G [02:29<00:00, 69.8MB/s]
100%|██████████████████████████████████████| 9.29G/9.29G [02:29<00:00, 66.6MB/s]


In [2]:
!pip install --user opencv-python
import cv2
import os

In [8]:
!unzip ./celeb-df-v2.zip
base_directory = "./"

Archive:  ./celeb-df-v2.zip
  inflating: Celeb-real/id0_0000.mp4  
  inflating: Celeb-real/id0_0001.mp4  
  inflating: Celeb-real/id0_0002.mp4  
  inflating: Celeb-real/id0_0003.mp4  
  inflating: Celeb-real/id0_0004.mp4  
  inflating: Celeb-real/id0_0005.mp4  
  inflating: Celeb-real/id0_0006.mp4  
  inflating: Celeb-real/id0_0007.mp4  
  inflating: Celeb-real/id0_0008.mp4  
  inflating: Celeb-real/id0_0009.mp4  
  inflating: Celeb-real/id10_0000.mp4  
  inflating: Celeb-real/id10_0001.mp4  
  inflating: Celeb-real/id10_0002.mp4  
  inflating: Celeb-real/id10_0003.mp4  
  inflating: Celeb-real/id10_0004.mp4  
  inflating: Celeb-real/id10_0005.mp4  
  inflating: Celeb-real/id10_0006.mp4  
  inflating: Celeb-real/id10_0007.mp4  
  inflating: Celeb-real/id10_0008.mp4  
  inflating: Celeb-real/id10_0009.mp4  
  inflating: Celeb-real/id11_0000.mp4  
  inflating: Celeb-real/id11_0001.mp4  
  inflating: Celeb-real/id11_0002.mp4  
  inflating: Celeb-real/id11_0003.mp4  
  inflating: Celeb-rea

In [11]:
!find /scratch/ag9961/Celeb-real -type f | tail -n +501 | xargs rm

In [13]:
!find /scratch/ag9961/Celeb-synthesis -type f | tail -n +501 | xargs rm

In [14]:
output_directory = "extracted_frames"

In [15]:
def process_videos_with_labels(base_dir, output_base_dir, frame_rate=1, resize_dim=(224, 224)):
    """
    Process videos from subdirectories (e.g., 'real', 'fake') and extract frames.

    Args:
        base_dir (str): Base directory containing 'real' and 'fake' subdirectories.
        output_base_dir (str): Base directory to save extracted frames.
        frame_rate (int): Frame rate for extracting frames.
        resize_dim (tuple): Dimensions to resize the extracted frames.
    """
    if not os.path.exists(output_base_dir):
        os.makedirs(output_base_dir)

    for label in ['Celeb-real', 'Celeb-synthesis']:
        input_dir = os.path.join(base_dir, label)
        output_dir = os.path.join(output_base_dir, label)

        if not os.path.exists(input_dir):
            print(f"Directory {input_dir} does not exist. Skipping.")
            continue

        if not os.path.exists(output_dir):
            os.makedirs(output_dir)

        for video_file in os.listdir(input_dir):
            video_path = os.path.join(input_dir, video_file)

            if video_file.lower().endswith(('.mp4', '.avi', '.mov', '.mkv')):
                print(f"Processing {video_file} in {label}...")
                # Create a subdirectory for each video's frames
                video_name = os.path.splitext(video_file)[0]
                video_output_dir = os.path.join(output_dir, video_name)

                if not os.path.exists(video_output_dir):
                    os.makedirs(video_output_dir)

                extract_frames(video_path, video_output_dir, frame_rate, resize_dim)
            else:
                print(f"Skipping non-video file: {video_file}")

def extract_frames(video_path, output_dir, frame_rate=1, resize_dim=(224, 224)):
    """
    Extract frames from a video, resize them, and save to a directory.

    Args:
        video_path (str): Path to the input video file.
        output_dir (str): Directory to save the frames.
        frame_rate (int): Frame rate for extracting frames.
        resize_dim (tuple): Dimensions to resize the extracted frames.
    """
    video_capture = cv2.VideoCapture(video_path)
    fps = int(video_capture.get(cv2.CAP_PROP_FPS))
    interval = max(1, fps // frame_rate)

    frame_count = 0
    success = True

    while success:
        success, frame = video_capture.read()
        if success and frame_count % interval == 0:
            resized_frame = cv2.resize(frame, resize_dim)
            frame_filename = os.path.join(output_dir, f"frame_{frame_count:04d}.jpg")
            cv2.imwrite(frame_filename, resized_frame)
        frame_count += 1

    video_capture.release()
    print(f"Frames from {video_path} saved to {output_dir}")

In [16]:
process_videos_with_labels(base_directory, output_directory, frame_rate=1, resize_dim=(224, 224))

Processing id49_0006.mp4 in Celeb-real...
Frames from ./Celeb-real/id49_0006.mp4 saved to extracted_frames/Celeb-real/id49_0006
Processing id27_0008.mp4 in Celeb-real...
Frames from ./Celeb-real/id27_0008.mp4 saved to extracted_frames/Celeb-real/id27_0008
Processing id32_0000.mp4 in Celeb-real...
Frames from ./Celeb-real/id32_0000.mp4 saved to extracted_frames/Celeb-real/id32_0000
Processing id1_0006.mp4 in Celeb-real...
Frames from ./Celeb-real/id1_0006.mp4 saved to extracted_frames/Celeb-real/id1_0006
Processing id50_0006.mp4 in Celeb-real...
Frames from ./Celeb-real/id50_0006.mp4 saved to extracted_frames/Celeb-real/id50_0006
Processing id55_0006.mp4 in Celeb-real...
Frames from ./Celeb-real/id55_0006.mp4 saved to extracted_frames/Celeb-real/id55_0006
Processing id0_0005.mp4 in Celeb-real...
Frames from ./Celeb-real/id0_0005.mp4 saved to extracted_frames/Celeb-real/id0_0005
Processing id32_0008.mp4 in Celeb-real...
Frames from ./Celeb-real/id32_0008.mp4 saved to extracted_frames/Cel

FRAME EXTRACTION

In [3]:
!pip install opencv-python opencv-python-headless


Defaulting to user installation because normal site-packages is not writeable


FRAME PROCESSING

In [4]:
!pip install facenet-pytorch


Defaulting to user installation because normal site-packages is not writeable


In [6]:

from facenet_pytorch import MTCNN
from PIL import Image
import os
import numpy as np
import torch
import torchvision

In [7]:
# Initialize MTCNN for face detection
mtcnn = MTCNN(keep_all=True, device='cuda' if torch.cuda.is_available() else 'cpu')

In [8]:
# Base paths
extracted_frames_path = "extracted_frames"  # Path containing 'real' and 'fake' subdirectories
processed_frames_base_path = "processed_frames"  # Base path to save processed frames

def process_frames_for_label(label, extracted_frames_path, processed_frames_path, target_size=(224, 224)):
    """
    Process frames for a given label ('real' or 'fake').

    Args:
        label (str): The label (e.g., 'real', 'fake').
        extracted_frames_path (str): Path to the extracted frames for this label.
        processed_frames_path (str): Path to save processed frames for this label.
        target_size (tuple): Target size for resized face images.
    """
    input_dir = os.path.join(extracted_frames_path, label)
    output_dir = os.path.join(processed_frames_path, label)

    if not os.path.exists(output_dir):
        os.makedirs(output_dir)

    for video_folder in os.listdir(input_dir):
        video_input_dir = os.path.join(input_dir, video_folder)
        video_output_dir = os.path.join(output_dir, video_folder)

        if not os.path.exists(video_output_dir):
            os.makedirs(video_output_dir)

        for frame_file in os.listdir(video_input_dir):
            frame_path = os.path.join(video_input_dir, frame_file)
            try:
                frame = Image.open(frame_path)  # Open the frame as an image
                faces, _ = mtcnn.detect(frame)  # Detect faces

                if faces is not None:
                    for i, box in enumerate(faces):
                        x1, y1, x2, y2 = [int(coord) for coord in box]  # Get bounding box
                        cropped_face = frame.crop((x1, y1, x2, y2))  # Crop the face
                        resized_face = cropped_face.resize(target_size)  # Resize the face
                        face_filename = f"{os.path.splitext(frame_file)[0]}_face_{i}.jpg"
                        resized_face.save(os.path.join(video_output_dir, face_filename))  # Save the face
                        print(f"Processed and saved: {face_filename}")
                else:
                    print(f"No faces detected in frame: {frame_file}")
            except Exception as e:
                print(f"Error processing frame {frame_file}: {e}")

def process_all_frames(extracted_frames_path, processed_frames_base_path, target_size=(224, 224)):
    """
    Process frames for both 'real' and 'fake' labels.

    Args:
        extracted_frames_path (str): Base path containing extracted frames.
        processed_frames_base_path (str): Base path to save processed frames.
        target_size (tuple): Target size for resized face images.
    """
    for label in ['Celeb-real', 'Celeb-synthesis']:
        print(f"Processing {label} frames...")
        process_frames_for_label(label, extracted_frames_path, processed_frames_base_path, target_size)

# Call the function to process all frames
process_all_frames(extracted_frames_path, processed_frames_base_path)

Processing Celeb-real frames...
Processed and saved: frame_0270_face_0.jpg
Processed and saved: frame_0000_face_0.jpg
Processed and saved: frame_0210_face_0.jpg
Processed and saved: frame_0120_face_0.jpg
Processed and saved: frame_0150_face_0.jpg
Processed and saved: frame_0180_face_0.jpg
Processed and saved: frame_0030_face_0.jpg
Processed and saved: frame_0090_face_0.jpg
Processed and saved: frame_0060_face_0.jpg
Processed and saved: frame_0240_face_0.jpg
Processed and saved: frame_0270_face_0.jpg
Processed and saved: frame_0300_face_0.jpg
Processed and saved: frame_0000_face_0.jpg
Processed and saved: frame_0210_face_0.jpg
Processed and saved: frame_0120_face_0.jpg
Processed and saved: frame_0150_face_0.jpg
Processed and saved: frame_0180_face_0.jpg
Processed and saved: frame_0030_face_0.jpg
Processed and saved: frame_0090_face_0.jpg
Processed and saved: frame_0060_face_0.jpg
Processed and saved: frame_0330_face_0.jpg
Processed and saved: frame_0240_face_0.jpg
Processed and saved: f

FRAMES : EXTRACTED vs PROCESSED

In [9]:
import cv2
# from google.colab.patches import cv2_imshow
import os

def display_original_and_processed_for_label(label, extracted_frames_path, processed_frames_path, num_frames=5):
    """
    Display original and processed frames side by side for a given label ('real' or 'fake').

    Args:
        label (str): The label ('real' or 'fake').
        extracted_frames_path (str): Path to the original frames.
        processed_frames_path (str): Path to the processed frames.
        num_frames (int): Number of frames to display from each video.
    """
    input_dir = os.path.join(extracted_frames_path, label)
    processed_dir = os.path.join(processed_frames_path, label)

    for video_folder in os.listdir(input_dir):
        video_input_dir = os.path.join(input_dir, video_folder)
        video_processed_dir = os.path.join(processed_dir, video_folder)

        if not os.path.exists(video_processed_dir):
            print(f"Processed directory does not exist for {video_folder}. Skipping...")
            continue

        # List the frames in both directories
        original_frames = sorted(os.listdir(video_input_dir))[:num_frames]
        processed_frames = sorted(os.listdir(video_processed_dir))[:num_frames]

        for original_file, processed_file in zip(original_frames, processed_frames):
            # Load the original and processed images
            original_path = os.path.join(video_input_dir, original_file)
            processed_path = os.path.join(video_processed_dir, processed_file)

            original_image = cv2.imread(original_path)
            processed_image = cv2.imread(processed_path)

            # Resize processed image to match original's height for display
            processed_resized = cv2.resize(processed_image, (original_image.shape[1] // 2, original_image.shape[0]))

            # Concatenate the images horizontally
            combined = cv2.hconcat([original_image, processed_resized])

            # Display the combined image
            print(f"Displaying: {original_file} (left) and {processed_file} (right)")
            # cv2_imshow(combined)

def display_all_labels(extracted_frames_path, processed_frames_path, num_frames=5):
    """
    Display original and processed frames side by side for both 'real' and 'fake' labels.

    Args:
        extracted_frames_path (str): Path to original frames (with 'real' and 'fake' subdirectories).
        processed_frames_path (str): Path to processed frames (with 'real' and 'fake' subdirectories).
        num_frames (int): Number of frames to display from each video.
    """
    for label in ['Celeb-real', 'Celeb-synthesis']:
        print(f"Displaying frames for {label}...")
        display_original_and_processed_for_label(label, extracted_frames_path, processed_frames_path, num_frames)

# Call the function to display side-by-side comparisons for all labels
display_all_labels(extracted_frames_path, processed_frames_base_path, num_frames=5)


Displaying frames for Celeb-real...
Displaying: frame_0000.jpg (left) and frame_0000_face_0.jpg (right)
Displaying: frame_0030.jpg (left) and frame_0030_face_0.jpg (right)
Displaying: frame_0060.jpg (left) and frame_0060_face_0.jpg (right)
Displaying: frame_0090.jpg (left) and frame_0090_face_0.jpg (right)
Displaying: frame_0120.jpg (left) and frame_0120_face_0.jpg (right)
Displaying: frame_0000.jpg (left) and frame_0000_face_0.jpg (right)
Displaying: frame_0030.jpg (left) and frame_0030_face_0.jpg (right)
Displaying: frame_0060.jpg (left) and frame_0060_face_0.jpg (right)
Displaying: frame_0090.jpg (left) and frame_0090_face_0.jpg (right)
Displaying: frame_0120.jpg (left) and frame_0120_face_0.jpg (right)
Displaying: frame_0000.jpg (left) and frame_0000_face_0.jpg (right)
Displaying: frame_0029.jpg (left) and frame_0029_face_0.jpg (right)
Displaying: frame_0058.jpg (left) and frame_0058_face_0.jpg (right)
Displaying: frame_0087.jpg (left) and frame_0087_face_0.jpg (right)
Displaying: 

DATA AUGMENTATION

In [5]:
from PIL import ImageOps, ImageEnhance, ImageFilter
import os
import random
import numpy as np
# from google.colab.patches import cv2_imshow

In [ ]:
import os
from PIL import Image, ImageOps, ImageEnhance, ImageFilter
import numpy as np

# Augmentation function
def augment_image(image):
    augmentations = []

    # Horizontal Flip
    flipped = ImageOps.mirror(image)
    augmentations.append(flipped)

    # Rotation
    rotated = image.rotate(np.random.uniform(-15, 15))
    augmentations.append(rotated)

    # Brightness Adjustment
    enhancer = ImageEnhance.Brightness(image)
    brightness_adjusted = enhancer.enhance(np.random.uniform(0.7, 1.3))
    augmentations.append(brightness_adjusted)

    # Gaussian Blur
    blurred = image.filter(ImageFilter.GaussianBlur(radius=2))
    augmentations.append(blurred)

    # Random Crop
    crop_size = (np.random.randint(10, 30), np.random.randint(10, 30))
    cropped = image.crop((crop_size[0], crop_size[1], image.width - crop_size[0], image.height - crop_size[1]))
    cropped = cropped.resize(image.size)
    augmentations.append(cropped)

    return augmentations

# Paths
processed_frames_base_path = "./processed_frames"
augmented_frames_base_path = "./augmented_frames"

# Create output directory
if not os.path.exists(augmented_frames_base_path):
    os.makedirs(augmented_frames_base_path)

# # Apply augmentation
# for file_name in os.listdir(processed_frames_path):
#     image_path = os.path.join(processed_frames_path, file_name)
#     image = Image.open(image_path)

#     # Perform augmentations
#     augmented_images = augment_image(image)

#     # Save augmented images
#     for i, augmented_image in enumerate(augmented_images):
#         augmented_file_name = f"{os.path.splitext(file_name)[0]}_augmented_{i}.jpg"
#         augmented_image.save(os.path.join(augmented_frames_path, augmented_file_name))
#         print(f"Saved: {augmented_file_name}")


# Apply augmentation for both 'real' and 'fake' labels
for label in ['Celeb-real', 'Celeb-synthesis']:
    print(f"Processing {label} frames...")

    processed_frames_path = os.path.join(processed_frames_base_path, label)
    augmented_frames_path = os.path.join(augmented_frames_base_path, label)

    if not os.path.exists(augmented_frames_path):
        os.makedirs(augmented_frames_path)

    # Iterate through videos
    for video_folder in os.listdir(processed_frames_path):
        video_processed_path = os.path.join(processed_frames_path, video_folder)
        video_augmented_path = os.path.join(augmented_frames_path, video_folder)

        if not os.path.exists(video_augmented_path):
            os.makedirs(video_augmented_path)

        # Iterate through frames in the video folder
        for file_name in os.listdir(video_processed_path):
            image_path = os.path.join(video_processed_path, file_name)
            try:
                image = Image.open(image_path)

                # Perform augmentations
                augmented_images = augment_image(image)

                # Save augmented images
                for i, augmented_image in enumerate(augmented_images):
                    augmented_file_name = f"{os.path.splitext(file_name)[0]}_augmented_{i}.jpg"
                    augmented_image.save(os.path.join(video_augmented_path, augmented_file_name))
                    print(f"Saved: {augmented_file_name}")
            except Exception as e:
                print(f"Error processing file {file_name}: {e}")




Processing Celeb-real frames...
Saved: frame_0180_face_0_augmented_0.jpg
Saved: frame_0180_face_0_augmented_1.jpg
Saved: frame_0180_face_0_augmented_2.jpg
Saved: frame_0180_face_0_augmented_3.jpg
Saved: frame_0180_face_0_augmented_4.jpg
Saved: frame_0120_face_0_augmented_0.jpg
Saved: frame_0120_face_0_augmented_1.jpg
Saved: frame_0120_face_0_augmented_2.jpg
Saved: frame_0120_face_0_augmented_3.jpg
Saved: frame_0120_face_0_augmented_4.jpg
Saved: frame_0210_face_0_augmented_0.jpg
Saved: frame_0210_face_0_augmented_1.jpg
Saved: frame_0210_face_0_augmented_2.jpg
Saved: frame_0210_face_0_augmented_3.jpg
Saved: frame_0210_face_0_augmented_4.jpg
Saved: frame_0030_face_0_augmented_0.jpg
Saved: frame_0030_face_0_augmented_1.jpg
Saved: frame_0030_face_0_augmented_2.jpg
Saved: frame_0030_face_0_augmented_3.jpg
Saved: frame_0030_face_0_augmented_4.jpg
Saved: frame_0000_face_0_augmented_0.jpg
Saved: frame_0000_face_0_augmented_1.jpg
Saved: frame_0000_face_0_augmented_2.jpg
Saved: frame_0000_face_0_

In [ ]:
import os
import cv2
# from google.colab.patches import cv2_imshow

def display_side_by_side_for_label(label, processed_frames_path, augmented_frames_path, num_samples=5):
    """
    Display processed and augmented frames side by side for a given label ('real' or 'fake').

    Args:
        label (str): The label ('real' or 'fake').
        processed_frames_path (str): Base directory containing processed frames.
        augmented_frames_path (str): Base directory containing augmented frames.
        num_samples (int): Number of samples to display per video folder.
    """
    processed_dir = os.path.join(processed_frames_path, label)
    augmented_dir = os.path.join(augmented_frames_path, label)

    for video_folder in os.listdir(processed_dir):
        video_processed_dir = os.path.join(processed_dir, video_folder)
        video_augmented_dir = os.path.join(augmented_dir, video_folder)

        if not os.path.exists(video_augmented_dir):
            print(f"Augmented directory does not exist for {video_folder}. Skipping...")
            continue

        processed_files = sorted(os.listdir(video_processed_dir))
        augmented_files = sorted(os.listdir(video_augmented_dir))

        # Group augmented files by their base name
        augmented_groups = {}
        for augmented_file in augmented_files:
            base_name = "_".join(augmented_file.split("_")[:-2])  # Extract base name (e.g., "frame_1_face_0")
            if base_name not in augmented_groups:
                augmented_groups[base_name] = []
            augmented_groups[base_name].append(augmented_file)

        # Process the first num_samples files
        for i, processed_file in enumerate(processed_files[:num_samples]):
            # Load the processed image
            processed_image = cv2.imread(os.path.join(video_processed_dir, processed_file))

            # Find matching augmented files
            base_name = os.path.splitext(processed_file)[0]
            if base_name in augmented_groups:
                for augmented_file in augmented_groups[base_name]:
                    # Load augmented image
                    augmented_image = cv2.imread(os.path.join(video_augmented_dir, augmented_file))

                    # Resize augmented image to match processed image height
                    augmented_image = cv2.resize(augmented_image, (processed_image.shape[1], processed_image.shape[0]))

                    # Concatenate images horizontally
                    combined = cv2.hconcat([processed_image, augmented_image])

                    # Display combined image
                    print(f"Displaying {processed_file} (processed) and {augmented_file} (augmented)")
                    # cv2_imshow(combined)
            else:
                print(f"No matching augmented files found for {processed_file}")

def display_side_by_side_all_labels(processed_frames_path, augmented_frames_path, num_samples=5):
    """
    Display processed and augmented frames side by side for both 'real' and 'fake' labels.

    Args:
        processed_frames_path (str): Path to processed frames (with 'real' and 'fake' subdirectories).
        augmented_frames_path (str): Path to augmented frames (with 'real' and 'fake' subdirectories).
        num_samples (int): Number of samples to display per video folder.
    """
    for label in ['Celeb-real', 'Celeb-synthesis']:
        print(f"Displaying side-by-side comparisons for {label} frames...")
        display_side_by_side_for_label(label, processed_frames_path, augmented_frames_path, num_samples)

# Call the function to display side-by-side comparisons for all labels
display_side_by_side_all_labels(processed_frames_base_path, augmented_frames_base_path, num_samples=5)


FEATURE EXTRACTION

In [8]:
import torch
import torchvision.models as models
from torchvision import transforms
from PIL import Image
import os
import numpy as np

# Load Pre-trained Model (ResNet Example)
model = models.resnet50(pretrained=True)
model = torch.nn.Sequential(*list(model.children())[:-1])  # Remove the final classification layer
model.eval()  # Set model to evaluation mode

# Define Preprocessing for Feature Extraction
preprocess = transforms.Compose([
    transforms.Resize((224, 224)),  # Resize to model input size
    transforms.ToTensor(),
    transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225])  # Standard normalization
])

# Directory paths
processed_frames_path = "./processed_frames"  # Path to processed frames
features_base_path = "./features"  # Path to save extracted features
features_output_path = "./features"
if not os.path.exists(features_output_path):
    os.makedirs(features_output_path)


/home/ag9961/.local/lib/python3.9/site-packages/torchvision/models/_utils.py:208: UserWarning: The parameter 'pretrained' is deprecated since 0.13 and may be removed in the future, please use 'weights' instead.
  warnings.warn(
/home/ag9961/.local/lib/python3.9/site-packages/torchvision/models/_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=ResNet50_Weights.IMAGENET1K_V1`. You can also use `weights=ResNet50_Weights.DEFAULT` to get the most up-to-date weights.
  warnings.warn(msg)


In [9]:
def extract_features_for_label(label, processed_frames_path, features_output_path):
    """
    Extract features for all processed frames under a given label ('real' or 'fake').

    Args:
        label (str): The label ('real' or 'fake').
        processed_frames_path (str): Path to processed frames.
        features_output_path (str): Path to save extracted features.
    """
    label_processed_path = os.path.join(processed_frames_path, label)
    label_features_path = os.path.join(features_output_path, label)

    if not os.path.exists(label_features_path):
        os.makedirs(label_features_path)

    for video_folder in os.listdir(label_processed_path):
        video_processed_path = os.path.join(label_processed_path, video_folder)
        video_features_path = os.path.join(label_features_path, video_folder)

        if not os.path.exists(video_features_path):
            os.makedirs(video_features_path)

        # Process each frame in the video folder
        for frame_file in os.listdir(video_processed_path):
            frame_path = os.path.join(video_processed_path, frame_file)
            try:
                # Load and preprocess the image
                image = Image.open(frame_path).convert("RGB")
                input_tensor = preprocess(image).unsqueeze(0)  # Add batch dimension

                # Extract features
                with torch.no_grad():
                    features = model(input_tensor)
                    features = features.squeeze().numpy()  # Convert to NumPy array

                # Save features to .npy file
                feature_file = os.path.splitext(frame_file)[0] + ".npy"
                np.save(os.path.join(video_features_path, feature_file), features)
                print(f"Features saved for {frame_file} -> {feature_file}")
            except Exception as e:
                print(f"Error processing {frame_file}: {e}")

def extract_features_all_labels(processed_frames_path, features_output_path):
    """
    Extract features for both 'real' and 'fake' labels.

    Args:
        processed_frames_path (str): Path to processed frames.
        features_output_path (str): Path to save extracted features.
    """
    for label in ['Celeb-real', 'Celeb-synthesis']:
        print(f"Extracting features for {label} frames...")
        extract_features_for_label(label, processed_frames_path, features_output_path)

# Call the function to extract features
extract_features_all_labels(processed_frames_base_path, features_base_path)

Extracting features for Celeb-real frames...
Features saved for frame_0180_face_0.jpg -> frame_0180_face_0.npy
Features saved for frame_0120_face_0.jpg -> frame_0120_face_0.npy
Features saved for frame_0210_face_0.jpg -> frame_0210_face_0.npy
Features saved for frame_0030_face_0.jpg -> frame_0030_face_0.npy
Features saved for frame_0000_face_0.jpg -> frame_0000_face_0.npy
Features saved for frame_0150_face_0.jpg -> frame_0150_face_0.npy
Features saved for frame_0270_face_0.jpg -> frame_0270_face_0.npy
Features saved for frame_0240_face_0.jpg -> frame_0240_face_0.npy
Features saved for frame_0090_face_0.jpg -> frame_0090_face_0.npy
Features saved for frame_0060_face_0.jpg -> frame_0060_face_0.npy
Features saved for frame_0180_face_0.jpg -> frame_0180_face_0.npy
Features saved for frame_0120_face_0.jpg -> frame_0120_face_0.npy
Features saved for frame_0330_face_0.jpg -> frame_0330_face_0.npy
Features saved for frame_0210_face_0.jpg -> frame_0210_face_0.npy
Features saved for frame_0300_f

Aggregate spatial features for each video

In [10]:
import os
import numpy as np

# Paths
features_base_path = "./features"  # Base directory with 'real' and 'fake' subdirectories
output_sequences_base_path = "./sequences"  # Output directory for aggregated sequences

if not os.path.exists(output_sequences_base_path):
    os.makedirs(output_sequences_base_path)

def aggregate_features_for_label(label, features_dir, output_dir):
    """
    Aggregate features for all videos under a given label ('real' or 'fake').

    Args:
        label (str): The label ('real' or 'fake').
        features_dir (str): Path to the directory containing features.
        output_dir (str): Path to save aggregated feature sequences.
    """
    label_features_dir = os.path.join(features_dir, label)
    label_output_dir = os.path.join(output_dir, label)

    if not os.path.exists(label_output_dir):
        os.makedirs(label_output_dir)

    for video_folder in os.listdir(label_features_dir):
        video_features_dir = os.path.join(label_features_dir, video_folder)
        video_output_dir = os.path.join(label_output_dir, video_folder)

        if not os.path.exists(video_features_dir):
            print(f"Features directory does not exist for {video_folder}. Skipping...")
            continue

        if not os.path.exists(video_output_dir):
            os.makedirs(video_output_dir)

        video_features = []
        for feature_file in sorted(os.listdir(video_features_dir)):  # Sort frames by frame number
            feature_path = os.path.join(video_features_dir, feature_file)
            try:
                features = np.load(feature_path)
                video_features.append(features)
            except Exception as e:
                print(f"Error loading features from {feature_file}: {e}")

        if video_features:
            video_features = np.array(video_features)  # Shape: (num_frames, feature_size)
            output_path = os.path.join(video_output_dir, "aggregated_features.npy")
            np.save(output_path, video_features)
            print(f"Saved aggregated features for {video_folder} to {output_path}")

def aggregate_features_all_labels(features_dir, output_dir):
    """
    Aggregate features for both 'real' and 'fake' labels.

    Args:
        features_dir (str): Path to the base directory containing features.
        output_dir (str): Path to save aggregated feature sequences.
    """
    for label in ['Celeb-real', 'Celeb-synthesis']:
        print(f"Aggregating features for {label} frames...")
        aggregate_features_for_label(label, features_dir, output_dir)

# Call the function to aggregate features for all labels
aggregate_features_all_labels(features_base_path, output_sequences_base_path)


Aggregating features for Celeb-real frames...
Saved aggregated features for id35_0005 to ./sequences/Celeb-real/id35_0005/aggregated_features.npy
Saved aggregated features for id46_0006 to ./sequences/Celeb-real/id46_0006/aggregated_features.npy
Saved aggregated features for id19_0006 to ./sequences/Celeb-real/id19_0006/aggregated_features.npy
Saved aggregated features for id61_0008 to ./sequences/Celeb-real/id61_0008/aggregated_features.npy
Saved aggregated features for id21_0009 to ./sequences/Celeb-real/id21_0009/aggregated_features.npy
Saved aggregated features for id27_0004 to ./sequences/Celeb-real/id27_0004/aggregated_features.npy
Saved aggregated features for id12_0001 to ./sequences/Celeb-real/id12_0001/aggregated_features.npy
Saved aggregated features for id0_0006 to ./sequences/Celeb-real/id0_0006/aggregated_features.npy
Saved aggregated features for id56_0007 to ./sequences/Celeb-real/id56_0007/aggregated_features.npy
Saved aggregated features for id4_0006 to ./sequences/Ce

Prepare dataset for temporal Modelling

In [11]:
from sklearn.model_selection import train_test_split
import os
import numpy as np

# Paths
output_sequences_base_path = "./sequences"  # Base directory containing aggregated feature sequences
filtered_labels_path = os.path.join(output_sequences_base_path, "filtered_labels.txt")

# Assign labels dynamically based on directory structure
video_paths = []
video_labels_list = []
filtered_labels = []

for label, dir_name in enumerate(['Celeb-real', 'Celeb-synthesis']):  # Assign 'real' -> 0 and 'fake' -> 1
    label_dir = os.path.join(output_sequences_base_path, dir_name)
    if not os.path.exists(label_dir):
        print(f"Directory {label_dir} does not exist. Skipping...")
        continue

    for video_folder in os.listdir(label_dir):
        video_path = os.path.join(label_dir, video_folder, "aggregated_features.npy")
        if os.path.exists(video_path):
            video_paths.append(video_path)
            video_labels_list.append(label)
            filtered_labels.append(f"{label} {video_folder}")
        else:
            print(f"Features file missing for {video_folder}, skipping...")

# Save dynamically generated labels to filtered_labels.txt
with open(filtered_labels_path, 'w') as f:
    for line in filtered_labels:
        f.write(line + '\n')
print(f"Filtered labels saved to {filtered_labels_path}")

# Split into train and test sets
X_train, X_test, y_train, y_test = train_test_split(video_paths, video_labels_list, test_size=0.2, random_state=42)

# Print summary
print(f"Train set: {len(X_train)} videos")
print(f"Test set: {len(X_test)} videos")

# Example: Print some paths and labels (optional)
# Uncomment the following lines to debug or inspect
print("Train examples:")
for path, label in zip(X_train[:5], y_train[:5]):
    print(f"Path: {path}, Label: {label}")
print("Test examples:")
for path, label in zip(X_test[:5], y_test[:5]):
    print(f"Path: {path}, Label: {label}")


Features file missing for id27_0005, skipping...
Filtered labels saved to ./sequences/filtered_labels.txt
Train set: 799 videos
Test set: 200 videos
Train examples:
Path: ./sequences/Celeb-synthesis/id20_id30_0008/aggregated_features.npy, Label: 1
Path: ./sequences/Celeb-real/id20_0004/aggregated_features.npy, Label: 0
Path: ./sequences/Celeb-real/id9_0000/aggregated_features.npy, Label: 0
Path: ./sequences/Celeb-synthesis/id22_id19_0006/aggregated_features.npy, Label: 1
Path: ./sequences/Celeb-real/id31_0009/aggregated_features.npy, Label: 0
Test examples:
Path: ./sequences/Celeb-real/id11_0002/aggregated_features.npy, Label: 0
Path: ./sequences/Celeb-synthesis/id20_id9_0002/aggregated_features.npy, Label: 1
Path: ./sequences/Celeb-real/id1_0002/aggregated_features.npy, Label: 0
Path: ./sequences/Celeb-real/id39_0006/aggregated_features.npy, Label: 0
Path: ./sequences/Celeb-synthesis/id30_id26_0001/aggregated_features.npy, Label: 1


In [12]:
import h5py
import numpy as np

# Save the data in an HDF5 file for faster processing and better RAM utilization
h5_file_path = "./data.h5"  # Update the path as needed
h5_file = h5py.File(h5_file_path, 'w')

# Function to load features and pad them to a consistent shape
def load_features_with_padding(paths):
    """
    Load features from .npy files and pad them to the maximum sequence length.

    Args:
        paths (list): List of paths to the .npy files.

    Returns:
        np.ndarray: Padded features array.
        list: Original lengths of the sequences before padding.
    """
    features = []
    lengths = []

    for path in paths:
        try:
            feature = np.load(path)
            features.append(feature)
            lengths.append(feature.shape[0])  # Record the number of frames
        except Exception as e:
            print(f"Error loading feature file {path}: {e}")

    # Find the maximum sequence length
    max_length = max(lengths)
    feature_dim = features[0].shape[1]  # Dimension of each feature vector

    # Pad sequences to have the same length
    padded_features = np.zeros((len(features), max_length, feature_dim))
    for i, feature in enumerate(features):
        padded_features[i, :feature.shape[0], :] = feature  # Pad only at the end

    return padded_features, lengths

# Load features for train and test sets
print("Loading training features...")
X_train_features, train_lengths = load_features_with_padding(X_train)
print("Loading testing features...")
X_test_features, test_lengths = load_features_with_padding(X_test)

# Save data into the HDF5 file
print("Saving data to HDF5...")
h5_file.create_dataset('X_train', data=X_train_features)
h5_file.create_dataset('X_test', data=X_test_features)
h5_file.create_dataset('y_train', data=np.array(y_train))
h5_file.create_dataset('y_test', data=np.array(y_test))
h5_file.create_dataset('train_lengths', data=np.array(train_lengths))  # Save original lengths
h5_file.create_dataset('test_lengths', data=np.array(test_lengths))    # Save original lengths

# Close the HDF5 file
h5_file.close()
print(f"Data saved to {h5_file_path}")


Loading training features...
Loading testing features...
Saving data to HDF5...
Data saved to ./data.h5


In [13]:
import gc
gc.collect()

770

Temporal Modelling

In [5]:
#Define LSTM model
# Import necessary modules
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import LSTM, Dense, Dropout, Masking, BatchNormalization, Bidirectional
from tensorflow.keras.regularizers import l2
from tensorflow.keras.callbacks import EarlyStopping, ReduceLROnPlateau

# Define the LSTM model
def create_lstm_model(input_shape):
    model = Sequential([
        Masking(mask_value=0., input_shape=input_shape),  # Mask padded frames
        Bidirectional(LSTM(128, return_sequences=True, kernel_regularizer=l2(0.01))),  # Bidirectional LSTM
        Dropout(0.5),  # Regularization
        BatchNormalization(),
        LSTM(64, return_sequences=False, kernel_regularizer=l2(0.01)),  # Second LSTM layer
        Dropout(0.5),
        Dense(64, activation='relu', kernel_regularizer=l2(0.01)),  # Fully connected layer
        Dropout(0.5),
        Dense(1, activation='sigmoid')  # Binary classification
    ])
    model.compile(optimizer='adam', loss='binary_crossentropy', metrics=['accuracy'])
    return model

# Create the model
input_shape = (None, 2048)  # Shape: (num_frames, feature_dim)
model = create_lstm_model(input_shape)
model.summary()

2024-12-19 16:36:08.433464: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1734644168.973629    5965 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1734644169.123014    5965 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2024-12-19 16:36:10.613250: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
/home/ag9961/.local/lib/python3.9/site-packages/keras/src/layers/core/masking.py:47: UserWarning: Do not pass an `input_shape

Model: "sequential"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ masking (Masking)               │ (None, None, 2048)     │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ bidirectional (Bidirectional)   │ (None, None, 256)      │     2,229,248 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout (Dropout)               │ (None, None, 256)      │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ batch_normalization             │ (None, None, 256)      │         1,024 │
│ (BatchNormalization)            │                        │               │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ lstm_1 (LSTM)                   │ (None, 64)             │        82,176 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_1 (Dropout)             │ (None, 64)             │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense (Dense)                   │ (None, 64)             │         4,160 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout_2 (Dropout)             │ (None, 64)             │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense_1 (Dense)                 │ (None, 1)              │            65 │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 2,316,673 (8.84 MB)

 Trainable params: 2,316,161 (8.84 MB)

 Non-trainable params: 512 (2.00 KB)

In [6]:
import h5py

h5_file_path = "./data.h5"  # Update this to your file path
with h5py.File(h5_file_path, 'r') as h5_file:
    print("Available datasets in the file:")
    print(list(h5_file.keys()))



Available datasets in the file:
['X_test', 'X_train', 'test_lengths', 'train_lengths', 'y_test', 'y_train']


In [7]:
from tensorflow.keras.preprocessing.sequence import pad_sequences
import h5py
import numpy as np
from sklearn.utils import class_weight

# Load data from the HDF5 file
h5_file_path = "./data.h5"  # Update this to your file path
with h5py.File(h5_file_path, 'r') as h5_file:
    X_train = np.array(h5_file['X_train'])
    y_train = np.array(h5_file['y_train'])
    X_test = np.array(h5_file['X_test'])
    y_test = np.array(h5_file['y_test'])

# Determine the maximum sequence length
max_seq_length = max([x.shape[0] for x in X_train] + [x.shape[0] for x in X_test])

# Prepare training data
X_train_data = pad_sequences(X_train, maxlen=max_seq_length, padding='post', dtype='float32')
y_train_data = np.array(y_train)

# Prepare testing data
X_test_data = pad_sequences(X_test, maxlen=max_seq_length, padding='post', dtype='float32')
y_test_data = np.array(y_test)

# Normalize data to range [0, 1]
X_train_data = X_train_data / np.max(X_train_data)
X_test_data = X_test_data / np.max(X_test_data)

# Compute class weights for imbalance
class_weights = class_weight.compute_class_weight('balanced', classes=np.unique(y_train_data), y=y_train_data)

# Callbacks for better training
early_stop = EarlyStopping(monitor='val_loss', patience=5, restore_best_weights=True)
lr_scheduler = ReduceLROnPlateau(monitor='val_loss', factor=0.5, patience=3, min_lr=1e-6)

# Verify shapes
print(f"X_train_data shape: {X_train_data.shape}")
print(f"X_test_data shape: {X_test_data.shape}")

# Train the model
history = model.fit(
    X_train_data, y_train_data,
    validation_data=(X_test_data, y_test_data),
    class_weight=dict(enumerate(class_weights)),
    batch_size=32,  # Increased batch size
    epochs=30,
    callbacks=[early_stop, lr_scheduler]
)


X_train_data shape: (799, 51, 2048)
X_test_data shape: (200, 51, 2048)
Epoch 1/30
25/25 ━━━━━━━━━━━━━━━━━━━━ 9s 143ms/step - accuracy: 0.5211 - loss: 15.6981 - val_accuracy: 0.4700 - val_loss: 6.1887 - learning_rate: 0.0010
Epoch 2/30
25/25 ━━━━━━━━━━━━━━━━━━━━ 3s 109ms/step - accuracy: 0.5633 - loss: 4.9393 - val_accuracy: 0.4850 - val_loss: 2.7420 - learning_rate: 0.0010
Epoch 3/30
25/25 ━━━━━━━━━━━━━━━━━━━━ 3s 109ms/step - accuracy: 0.5678 - loss: 2.4769 - val_accuracy: 0.6700 - val_loss: 1.9098 - learning_rate: 0.0010
Epoch 4/30
25/25 ━━━━━━━━━━━━━━━━━━━━ 3s 109ms/step - accuracy: 0.5864 - loss: 1.7831 - val_accuracy: 0.5400 - val_loss: 1.5277 - learning_rate: 0.0010
Epoch 5/30
25/25 ━━━━━━━━━━━━━━━━━━━━ 3s 108ms/step - accuracy: 0.6155 - loss: 1.4519 - val_accuracy: 0.6100 - val_loss: 1.2942 - learning_rate: 0.0010
Epoch 6/30
25/25 ━━━━━━━━━━━━━━━━━━━━ 3s 110ms/step - accuracy: 0.6923 - loss: 1.2146 - val_accuracy: 0.5350 - val_loss: 1.1927 - learning_rate: 0.0010
Epoch 7/30
25/25

In [8]:
#evaluate the model
# Evaluate the model
test_loss, test_accuracy = model.evaluate(X_test_data, y_test_data)
print(f"Test Loss: {test_loss}, Test Accuracy: {test_accuracy}")


7/7 ━━━━━━━━━━━━━━━━━━━━ 0s 38ms/step - accuracy: 0.7274 - loss: 0.7206
Test Loss: 0.7324844598770142, Test Accuracy: 0.7099999785423279


In [9]:
model.save('lstm_model.h5')  # Save the model to a file
print("Model saved as 'lstm_model.h5'")

Model saved as 'lstm_model.h5'


GAN

In [11]:
import h5py
import numpy as np
import tensorflow as tf
from tensorflow.keras.models import Model
from tensorflow.keras.layers import Input, Dense, LeakyReLU, Reshape, Flatten
from tensorflow.keras.optimizers import Adam
import os

# Latent dimension and feature shape
latent_dim = 10

# Load data from HDF5 file
h5_file_path = "./data.h5"  # Update this to your file path
with h5py.File(h5_file_path, 'r') as h5_file:
    X_train = np.array(h5_file['X_train'], dtype=np.float32)  # Ensure dtype is float32
    X_train = (X_train - 0.5) * 2  # Normalize to [-1, 1] for GAN training

# Automatically infer feature shape
feature_shape = X_train.shape[1:]
print(f"Inferred feature shape: {feature_shape}")

# Build Generator
def build_generator(latent_dim, feature_shape):
    generator_input = Input(shape=(latent_dim,))
    x = Dense(256)(generator_input)
    x = LeakyReLU()(x)
    x = Dense(512)(x)
    x = LeakyReLU()(x)
    num_units = np.prod(feature_shape)
    generated_features = Dense(num_units, activation='tanh')(x)
    generated_features = Reshape(feature_shape)(generated_features)
    return Model(generator_input, generated_features, name="Generator")

# Build Discriminator
def build_discriminator(input_shape):
    discriminator_input = Input(shape=input_shape)
    x = Flatten()(discriminator_input)
    x = Dense(512)(x)
    x = LeakyReLU()(x)
    x = Dense(256)(x)
    x = LeakyReLU()(x)
    validity = Dense(1, activation='sigmoid')(x)
    return Model(discriminator_input, validity, name="Discriminator")

# Initialize models
generator = build_generator(latent_dim, feature_shape)
discriminator = build_discriminator(feature_shape)

# Optimizers
gen_optimizer = Adam(0.0002, 0.5)
disc_optimizer = Adam(0.0002, 0.5)

# Loss function
loss_fn = tf.keras.losses.BinaryCrossentropy()

# Sample images
def sample_images(generator, latent_dim, epoch, output_dir="gan_images"):
    os.makedirs(output_dir, exist_ok=True)
    noise = np.random.normal(0, 1, (16, latent_dim)).astype(np.float32)
    generated_features = generator.predict(noise)
    np.save(f"{output_dir}/generated_epoch_{epoch}.npy", generated_features)
    print(f"Generated samples saved at epoch {epoch}.")

# Train step
@tf.function
def train_step(generator, discriminator, gen_optimizer, disc_optimizer, real_features, latent_dim):
    # Generate fake data
    batch_size = real_features.shape[0]
    noise = tf.random.normal((batch_size, latent_dim))
    fake_features = generator(noise)

    # Labels
    real_labels = tf.ones((batch_size, 1))
    fake_labels = tf.zeros((batch_size, 1))

    # Train discriminator
    with tf.GradientTape() as tape:
        real_loss = loss_fn(real_labels, discriminator(real_features))
        fake_loss = loss_fn(fake_labels, discriminator(fake_features))
        disc_loss = 0.5 * (real_loss + fake_loss)
    grads = tape.gradient(disc_loss, discriminator.trainable_variables)
    disc_optimizer.apply_gradients(zip(grads, discriminator.trainable_variables))

    # Train generator
    with tf.GradientTape() as tape:
        noise = tf.random.normal((batch_size, latent_dim))
        generated_features = generator(noise)
        valid_labels = tf.ones((batch_size, 1))  # Generator wants discriminator to see fakes as real
        gen_loss = loss_fn(valid_labels, discriminator(generated_features))
    grads = tape.gradient(gen_loss, generator.trainable_variables)
    gen_optimizer.apply_gradients(zip(grads, generator.trainable_variables))

    return disc_loss, gen_loss

# Training loop
def train_gan(generator, discriminator, gen_optimizer, disc_optimizer, X_train, latent_dim, epochs, batch_size, sample_interval):
    for epoch in range(1, epochs + 1):
        idx = np.random.randint(0, X_train.shape[0], batch_size)
        real_features = tf.convert_to_tensor(X_train[idx], dtype=tf.float32)

        # Perform a training step
        disc_loss, gen_loss = train_step(generator, discriminator, gen_optimizer, disc_optimizer, real_features, latent_dim)

        # Print progress
        if epoch % sample_interval == 0 or epoch == 1:
            print(f"Epoch {epoch}/{epochs} | D Loss: {disc_loss:.4f} | G Loss: {gen_loss:.4f}")
            sample_images(generator, latent_dim, epoch)

# Start training
train_gan(generator, discriminator, gen_optimizer, disc_optimizer, X_train, latent_dim, epochs=10, batch_size=32, sample_interval=10)

Inferred feature shape: (51, 2048)
Epoch 1/10 | D Loss: 0.6037 | G Loss: 0.7066
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 67ms/step
Generated samples saved at epoch 1.
Epoch 10/10 | D Loss: 0.9655 | G Loss: 0.7516
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 38ms/step
Generated samples saved at epoch 10.


**TRANSFORMERS**

In [12]:
import torch
import h5py
import torch.nn as nn
from torchvision import models
from torch.utils.data import DataLoader, Dataset
from einops import rearrange
import numpy as np
from torch.nn.utils.rnn import pad_sequence
h5_file_path = "./data.h5"  # Update this to your file path
with h5py.File(h5_file_path, 'r') as h5_file:
    X_train = np.array(h5_file['X_train'])  # Load features from the HDF5 file
    y_train = np.array(h5_file['y_train'])
    y_test = np.array(h5_file['y_test'])
    X_test = np.array(h5_file['X_test'])
    

class VideoDataset(Dataset):
    def __init__(self, file_paths, labels):
        # Check if file_paths contains actual data or file paths
        if isinstance(file_paths[0], str):
            self.file_paths = file_paths
            self.load_from_file = True
        else:
            self.file_paths = [torch.tensor(fp, dtype=torch.float32) for fp in file_paths]
            self.load_from_file = False

        self.labels = torch.tensor(labels, dtype=torch.long)

    def __len__(self):
        return len(self.file_paths)

    def __getitem__(self, idx):
        if self.load_from_file:
            # Load the .npy file if file_paths are paths
            features = np.load(self.file_paths[idx]).astype(np.float32)
            features = torch.tensor(features)  # Convert to tensor
        else:
            # Use preloaded data directly
            features = self.file_paths[idx]

        label = self.labels[idx]
        return features, label


# Custom collate function for padding
def pad_collate_fn(batch):
    features, labels = zip(*batch)
    padded_features = pad_sequence(features, batch_first=True)  # Pad to the same length
    labels = torch.tensor(labels, dtype=torch.long)
    return padded_features, labels

class Residual(nn.Module):
    def __init__(self, fn):
        super().__init__()
        self.fn = fn

    def forward(self, x, **kwargs):
        return self.fn(x, **kwargs) + x

class PreNorm(nn.Module):
    def __init__(self, dim, fn):
        super().__init__()
        self.norm = nn.LayerNorm(dim)
        self.fn = fn

    def forward(self, x, **kwargs):
        return self.fn(self.norm(x), **kwargs)

class FeedForward(nn.Module):
    def __init__(self, dim, hidden_dim):
        super().__init__()
        self.net = nn.Sequential(
            nn.Linear(dim, hidden_dim),
            nn.GELU(),
            nn.Linear(hidden_dim, dim)
        )

    def forward(self, x):
        return self.net(x)

class Attention(nn.Module):
    def __init__(self, dim, heads=8):
        super().__init__()
        self.heads = heads
        self.scale = dim ** -0.5

        self.to_qkv = nn.Linear(dim, dim * 3, bias=False)
        self.to_out = nn.Linear(dim, dim)

    def forward(self, x, mask=None):
        b, n, _, h = *x.shape, self.heads
        qkv = self.to_qkv(x)
        q, k, v = rearrange(qkv, 'b n (qkv h d) -> qkv b h n d', qkv=3, h=h)

        dots = torch.einsum('bhid,bhjd->bhij', q, k) * self.scale

        if mask is not None:
            dots.masked_fill_(~mask, float('-inf'))

        attn = dots.softmax(dim=-1)
        out = torch.einsum('bhij,bhjd->bhid', attn, v)
        out = rearrange(out, 'b h n d -> b n (h d)')
        return self.to_out(out)

class TemporalTransformer(nn.Module):
    def __init__(self, input_dim, num_classes, num_heads, num_layers, hidden_dim=2048, dropout=0.3):
        super(TemporalTransformer, self).__init__()

        # Positional Embeddings
        self.pos_embedding = nn.Parameter(torch.randn(1, 500, input_dim))  # Assuming max sequence length is 500
        self.dropout = nn.Dropout(dropout)

        # Transformer Layers
        self.layers = nn.ModuleList([
            nn.Sequential(
                Residual(PreNorm(input_dim, Attention(input_dim, heads=num_heads))),
                Residual(PreNorm(input_dim, FeedForward(input_dim, hidden_dim=hidden_dim)))
            ) for _ in range(num_layers)
        ])

        # Classification Head
        self.fc = nn.Linear(input_dim, num_classes)

    def forward(self, x):
        b, n, _ = x.shape
        x += self.pos_embedding[:, :n]
        x = self.dropout(x)

        for layer in self.layers:
            x = layer(x)

        x = x.mean(dim=1)  # Global Average Pooling
        return self.fc(x)

# Training and Evaluation
def mixup_data(x, y, alpha=0.4):
    lam = np.random.beta(alpha, alpha)
    index = torch.randperm(x.size(0)).to(x.device)
    mixed_x = lam * x + (1 - lam) * x[index, :]
    y_a, y_b = y, y[index]
    return mixed_x, y_a, y_b, lam

def mixup_criterion(criterion, pred, y_a, y_b, lam):
    return lam * criterion(pred, y_a) + (1 - lam) * criterion(pred, y_b)

def train_model(model, train_loader, criterion, optimizer, device):
    model.train()
    running_loss = 0.0
    for inputs, labels in train_loader:
        inputs, labels = inputs.to(device), labels.to(device)
        inputs, targets_a, targets_b, lam = mixup_data(inputs, labels)
    
        optimizer.zero_grad()
        outputs = model(inputs)
        loss = mixup_criterion(criterion, outputs, targets_a, targets_b, lam)
    
        loss.backward()
        torch.nn.utils.clip_grad_norm_(model.parameters(), max_norm=1.0)
        optimizer.step()
    
        running_loss += loss.item()

    return running_loss / len(train_loader)

def evaluate_model(model, test_loader, criterion, device):
    model.eval()
    running_loss = 0.0
    correct = 0
    total = 0
    with torch.no_grad():
        for inputs, labels in test_loader:
            inputs, labels = inputs.to(device), labels.to(device)
            outputs = model(inputs)
            loss = criterion(outputs, labels)
            running_loss += loss.item()

            _, predicted = torch.max(outputs, 1)
            total += labels.size(0)
            correct += (predicted == labels).sum().item()
    accuracy = correct / total
    return running_loss / len(test_loader), accuracy






/home/ag9961/.local/lib/python3.9/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [13]:
from transformers import get_linear_schedule_with_warmup
from torch.optim.lr_scheduler import ReduceLROnPlateau

train_dataset = VideoDataset(X_train, y_train)
test_dataset = VideoDataset(X_test, y_test)

train_loader = DataLoader(train_dataset, batch_size=16, shuffle=True, collate_fn=pad_collate_fn)
test_loader = DataLoader(test_dataset, batch_size=16, shuffle=False, collate_fn=pad_collate_fn)


device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

input_dim = 2048  # Update this to match your feature size
model = TemporalTransformer(input_dim=input_dim, num_classes=2, num_heads=8, num_layers=4).to(device)

criterion = nn.CrossEntropyLoss()
num_epochs = 50
optimizer = torch.optim.Adam(model.parameters(), lr=0.001, weight_decay=1e-4)
total_steps = len(train_loader) * num_epochs
warmup_steps = total_steps // 10  # 10% warmup

# scheduler = get_linear_schedule_with_warmup(optimizer, warmup_steps, total_steps)
scheduler = torch.optim.lr_scheduler.ReduceLROnPlateau(
    optimizer, mode='min', patience=3, factor=0.5, verbose=True
)

for epoch in range(num_epochs):
    train_loss = train_model(model, train_loader, criterion, optimizer, device)
    test_loss, test_accuracy = evaluate_model(model, test_loader, criterion, device)
    scheduler.step(test_loss)
    print(f"Epoch {epoch+1}/{num_epochs}, Train Loss: {train_loss:.4f}, Test Loss: {test_loss:.4f}, Test Accuracy: {test_accuracy:.4f}")



/home/ag9961/.local/lib/python3.9/site-packages/torch/optim/lr_scheduler.py:28: UserWarning: The verbose parameter is deprecated. Please use get_last_lr() to access the learning rate.
  warnings.warn("The verbose parameter is deprecated. Please use get_last_lr() "


Epoch 1/50, Train Loss: 9.8747, Test Loss: 0.8581, Test Accuracy: 0.4900
Epoch 2/50, Train Loss: 5.9929, Test Loss: 4.3825, Test Accuracy: 0.4700
Epoch 3/50, Train Loss: 1.8742, Test Loss: 3.4803, Test Accuracy: 0.4700
Epoch 4/50, Train Loss: 1.1575, Test Loss: 0.8363, Test Accuracy: 0.5300
Epoch 5/50, Train Loss: 0.8557, Test Loss: 0.8513, Test Accuracy: 0.4700
Epoch 6/50, Train Loss: 1.1534, Test Loss: 3.6221, Test Accuracy: 0.4700
Epoch 7/50, Train Loss: 2.5083, Test Loss: 6.9282, Test Accuracy: 0.5300
Epoch 8/50, Train Loss: 1.6110, Test Loss: 0.7429, Test Accuracy: 0.4700
Epoch 9/50, Train Loss: 1.5110, Test Loss: 0.7809, Test Accuracy: 0.4700
Epoch 10/50, Train Loss: 1.5027, Test Loss: 0.7558, Test Accuracy: 0.4850
Epoch 11/50, Train Loss: 0.8819, Test Loss: 2.1733, Test Accuracy: 0.5700
Epoch 12/50, Train Loss: 1.8420, Test Loss: 0.7171, Test Accuracy: 0.5350
Epoch 13/50, Train Loss: 1.2260, Test Loss: 1.0807, Test Accuracy: 0.4700
Epoch 14/50, Train Loss: 1.8773, Test Loss: 0.7

In [14]:
torch.save(model.state_dict(), "transformer_model.h5")
print("Model weights saved as 'transformer_model.h5'")

Model weights saved as 'transformer_model.h5'


In [15]:
torch.save(model, "temporal_transformer_complete.pth")
print("Entire model saved to 'temporal_transformer_complete.pth'")

Entire model saved to 'temporal_transformer_complete.pth'


CViT

In [17]:
import torch
import torch.nn as nn
from torchvision import models
from torch.utils.data import DataLoader, Dataset
from einops import rearrange
import numpy as np
from torch.optim.lr_scheduler import StepLR


class Residual(nn.Module):
    def __init__(self, fn):
        super().__init__()
        self.fn = fn

    def forward(self, x, **kwargs):
        return self.fn(x, **kwargs) + x

class PreNorm(nn.Module):
    def __init__(self, dim, fn):
        super().__init__()
        self.norm = nn.LayerNorm(dim)
        self.fn = fn

    def forward(self, x, **kwargs):
        return self.fn(self.norm(x), **kwargs)

class FeedForward(nn.Module):
    def __init__(self, dim, hidden_dim):
        super().__init__()
        self.net = nn.Sequential(
            nn.Linear(dim, hidden_dim),
            nn.GELU(),
            nn.Linear(hidden_dim, dim)
        )

    def forward(self, x):
        return self.net(x)

class Attention(nn.Module):
    def __init__(self, dim, heads=8):
        super().__init__()
        self.heads = heads
        self.scale = dim ** -0.5

        self.to_qkv = nn.Linear(dim, dim * 3, bias=False)
        self.to_out = nn.Linear(dim, dim)

    def forward(self, x, mask=None):
        b, n, _, h = *x.shape, self.heads
        qkv = self.to_qkv(x)
        q, k, v = rearrange(qkv, 'b n (qkv h d) -> qkv b h n d', qkv=3, h=h)

        dots = torch.einsum('bhid,bhjd->bhij', q, k) * self.scale

        if mask is not None:
            dots.masked_fill_(~mask, float('-inf'))

        attn = dots.softmax(dim=-1)
        out = torch.einsum('bhij,bhjd->bhid', attn, v)
        out = rearrange(out, 'b h n d -> b n (h d)')
        return self.to_out(out)

class Transformer(nn.Module):
    def __init__(self, dim, depth, heads, mlp_dim):
        super().__init__()
        self.layers = nn.ModuleList([])
        for _ in range(depth):
            self.layers.append(nn.ModuleList([
                Residual(PreNorm(dim, Attention(dim, heads=heads))),
                Residual(PreNorm(dim, FeedForward(dim, mlp_dim)))
            ]))

    def forward(self, x, mask=None):
        for attn, ff in self.layers:
            x = attn(x, mask=mask)
            x = ff(x)
        return x

class CViTForNumpy(nn.Module):
    

    def __init__(self, input_dim, num_classes, dim=512, depth=6, heads=8, mlp_dim=2048, dropout=0.1):
        super().__init__()

        # Input Embedding (for .npy features)
        self.feature_embedding = nn.Linear(input_dim, dim)
        self.cls_token = nn.Parameter(torch.randn(1, 1, dim))  
        self.dropout = nn.Dropout(0.3)  
        def sinusoidal_embedding(seq_len, dim):
            position = torch.arange(seq_len).unsqueeze(1)
            div_term = torch.exp(torch.arange(0, dim, 2) * (-np.log(10000.0) / dim))
            pe = torch.zeros(seq_len, dim)
            pe[:, 0::2] = torch.sin(position * div_term)
            pe[:, 1::2] = torch.cos(position * div_term)
            return pe.unsqueeze(0)
        self.pos_embedding = sinusoidal_embedding(500, dim)
        # Transformer Layers
        self.transformer = Transformer(dim=dim, depth=depth, heads=heads, mlp_dim=mlp_dim)

        # Classification Head
        self.mlp_head = nn.Sequential(
            nn.LayerNorm(dim),
            nn.Linear(dim, num_classes)
        )

    def forward(self, x):

    # Embed features
        x = self.feature_embedding(x)
    
        # Add positional embeddings (move to input's device)
        b, n, _ = x.shape
        x = x + self.pos_embedding[:, :n].to(x.device)
    
        # Dropout
        x = self.dropout(x)
    
        # Transformer
        x = self.transformer(x)
    
        # Global Average Pooling and Classification
        x = x.mean(dim=1)
        return self.mlp_head(x)


# Training and Evaluation

def train_model(model, train_loader, criterion, optimizer, device):
    model.train()
    running_loss = 0.0
    for inputs, labels in train_loader:
        inputs, labels = inputs.to(device), labels.to(device)

        optimizer.zero_grad()
        outputs = model(inputs)
        loss = criterion(outputs, labels)
        loss.backward()
        optimizer.step()

        running_loss += loss.item()
    return running_loss / len(train_loader)

def evaluate_model(model, test_loader, criterion, device):
    model.eval()
    running_loss = 0.0
    correct = 0
    total = 0
    with torch.no_grad():
        for inputs, labels in test_loader:
            inputs, labels = inputs.to(device), labels.to(device)
            outputs = model(inputs)
            loss = criterion(outputs, labels)
            running_loss += loss.item()

            _, predicted = torch.max(outputs, 1)
            total += labels.size(0)
            correct += (predicted == labels).sum().item()
    accuracy = correct / total
    return running_loss / len(test_loader), accuracy





In [18]:
!pip install transformers
from transformers import get_linear_schedule_with_warmup

Defaulting to user installation because normal site-packages is not writeable


In [19]:
train_dataset = VideoDataset(X_train, y_train)
test_dataset = VideoDataset(X_test, y_test)

train_loader = DataLoader(train_dataset, batch_size=16, shuffle=True, collate_fn=pad_collate_fn)
test_loader = DataLoader(test_dataset, batch_size=16, shuffle=False, collate_fn=pad_collate_fn)

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

input_dim = 2048  # Update this to match your feature size
model = CViTForNumpy(
    input_dim=input_dim,
    num_classes=2,
    dim=768,  # Increase dimension
    depth=12,  # Increase transformer depth
    heads=12,  # Increase heads
    mlp_dim=3072,  # Increase feedforward dimension
    dropout=0.2
).to(device)

# Optimizer with weight decay
optimizer = torch.optim.AdamW(model.parameters(), lr=0.0005, weight_decay=1e-4)

# Update CViT dropout


# Loss function
criterion = nn.CrossEntropyLoss(label_smoothing=0.1)
total_steps = len(train_loader) * num_epochs
warmup_steps = total_steps // 10

scheduler = get_linear_schedule_with_warmup(optimizer, num_warmup_steps=warmup_steps, num_training_steps=total_steps)

# Update train loop
for epoch in range(num_epochs):
    train_loss = train_model(model, train_loader, criterion, optimizer, device)
    test_loss, test_accuracy = evaluate_model(model, test_loader, criterion, device)
    optimizer.step()
    scheduler.step()
    print(f"Epoch {epoch+1}/{num_epochs}, Train Loss: {train_loss:.4f}, Test Loss: {test_loss:.4f}, Test Accuracy: {test_accuracy:.4f}")

Epoch 1/50, Train Loss: 0.7610, Test Loss: 0.7640, Test Accuracy: 0.5300
Epoch 2/50, Train Loss: 0.7649, Test Loss: 0.6963, Test Accuracy: 0.5300
Epoch 3/50, Train Loss: 0.7055, Test Loss: 0.6997, Test Accuracy: 0.4700
Epoch 4/50, Train Loss: 0.7060, Test Loss: 0.7038, Test Accuracy: 0.4700
Epoch 5/50, Train Loss: 0.7172, Test Loss: 0.6910, Test Accuracy: 0.4700
Epoch 6/50, Train Loss: 0.6970, Test Loss: 0.6789, Test Accuracy: 0.5950
Epoch 7/50, Train Loss: 0.7397, Test Loss: 0.6874, Test Accuracy: 0.5350
Epoch 8/50, Train Loss: 0.7119, Test Loss: 0.7189, Test Accuracy: 0.4700
Epoch 9/50, Train Loss: 0.7059, Test Loss: 0.6807, Test Accuracy: 0.6800
Epoch 10/50, Train Loss: 0.6994, Test Loss: 0.6863, Test Accuracy: 0.5400
Epoch 11/50, Train Loss: 0.7067, Test Loss: 0.6776, Test Accuracy: 0.6450
Epoch 12/50, Train Loss: 0.6965, Test Loss: 0.6934, Test Accuracy: 0.4700
Epoch 13/50, Train Loss: 0.7117, Test Loss: 0.6776, Test Accuracy: 0.5550
Epoch 14/50, Train Loss: 0.6958, Test Loss: 0.6